# Image Thumbnails from COSMOS

This notebook tutorial demonstrates the process of querying IRSA's Simple Image Access (SIA) service for the COSMOS images, making a cutout image (thumbnail), and displaying the cutout.

***

## Learning Goals

By the end of this tutorial, you will:

* Learn how to search the NASA Astronomical Virtual Observatory Directory web portal for a service that provides access to IRSA's COSMOS images.
* Use the Python pyvo package to identify which of IRSA's COSMOS images cover a specified coordinate.
* Download one of the identified images.
* Create and display a cutout of the downloaded image.

## Introduction

The COSMOS Archive serves data taken for the Cosmic Evolution Survey with HST (COSMOS) project, using IRSA's general search service, Atlas. COSMOS is an HST Treasury Project to survey a 2 square degree equatorial field with the ACS camera. For more information about COSMOS, see:

https://irsa.ipac.caltech.edu/Missions/cosmos.html

The [NASA/IPAC Infrared Science Archive (IRSA)](https://irsa.ipac.caltech.edu) at Caltech is one of the archives for COSMOS images and catalogs. The COSMOS images that are the subject of this tutorial are made accessible via the [International Virtual Observatory Alliance (IVOA)](https://ivoa.net) [Simple Image Access (SIA)](https://wiki.ivoa.net/internal/IVOA/SiaInterface/SIA-V2-Analysis.pdf) protocol. IRSA's SEIP SIA service is registered in the NASA Astronomical Virtual Observatory (NAVO) [Directory](https://vao.stsci.edu). Based on the registered information, the Python package [pyvo](https://pyvo.readthedocs.io) can be used to query the SIA service for a list of images that meet specified criteria, and standard Python libraries can be used to download and manipulate the images.
Other datasets at IRSA are available through other SIA services:

https://irsa.ipac.caltech.edu/docs/program_interface/api_images.html



## Imports

- *pyvo* for querying IRSA's COSMOS SIA service
- *astropy.coordinates* for defining coordinates
- *astropy.nddata* for creating an image cutout
- *astropy.wcs* for interpreting the World Coordinate System header keywords of a fits file
- *astropy.units* for attaching units to numbers passed to the SIA service
- *matplotlib.pyplot* for plotting
- *astropy.utils.data* for downloading files
- *astropy.io* to manipulate FITS files

In [ ]:
import pyvo as vo
from astropy.coordinates import SkyCoord
from astropy.nddata import Cutout2D
from astropy.wcs import WCS
import astropy.units as u
import matplotlib.pyplot as plt
from astropy.utils.data import download_file
from astropy.io import fits

## Section 1 - Setup

Set images to display in the notebook

In [ ]:
%matplotlib inline

Define coordinates of a bright source

In [ ]:
ra = 149.99986
dec = 2.24875
pos = SkyCoord(ra=ra, dec=dec, unit='deg')

## Section 2 - Lookup and define a service for COSMOS images

Start at STScI VAO Registry at https://vao.stsci.edu/keyword-search/

Limit by Publisher "NASA/IPAC Infrared Science Archive" and Capability Type "Simple Image Access Protocol" then search on "COSMOS"

Locate the SIA2 URL https://irsa.ipac.caltech.edu/cgi-bin/Atlas/nph-atlas?mission=COSMOS&hdr_location=%5CCOSMOSDataPath%5C&collection_desc=Cosmic+Evolution+Survey+with+HST+%28COSMOS%29&SIAP_ACTIVE=1&

In [ ]:
cosmos_service = vo.dal.SIAService("https://irsa.ipac.caltech.edu/cgi-bin/Atlas/nph-atlas?mission=COSMOS&hdr_location=%5CCOSMOSDataPath%5C&collection_desc=Cosmic+Evolution+Survey+with+HST+%28COSMOS%29&SIAP_ACTIVE=1&")

## Section 3 - Search the service

Search for images covering within 1 arcsecond of the star

In [ ]:
im_table = cosmos_service.search(pos=pos, size=1.0*u.arcsec)

Inspect the table of images that is returned

In [ ]:
im_table

In [ ]:
im_table.to_table().colnames

View the first ten entries of the table

In [ ]:
im_table.to_table()[:10]

## Section 4 - Locate and download an image of interest

Locate the first image in the band_name of i+

In [ ]:
for i in range(len(im_table)):
    if im_table[i]['band_name'] == 'i+':
        break
print(im_table[i].getdataurl())

Download the image

In [ ]:
fname = download_file(im_table[i].getdataurl(), cache=True)
image1 = fits.open(fname)

## Section 5 - Extract a cutout and plot it

In [ ]:
wcs = WCS(image1[0].header)

Make a cutout centered on the position

In [ ]:
cutout = Cutout2D(image1[0].data, pos, (60, 60), wcs=wcs)
wcs = cutout.wcs

In [ ]:
fig = plt.figure()

ax = fig.add_subplot(1, 1, 1, projection=wcs)
ax.imshow(cutout.data, cmap='gray_r', origin='lower')
ax.scatter(ra, dec, transform=ax.get_transform('fk5'), s=500, edgecolor='red', facecolor='none')


***

## About this notebook

**Author:** David Shupe, IRSA Scientist, and the IRSA Science Team

**Updated On:** 2022-02-14

**Contact:** irsasupport@ipac.caltech.edu or https://jira.ipac.caltech.edu/irsasupport

## Citations

If you use `astropy` for published research, please cite the authors. Follow these links for more information about citing `astropy`:

* [Citing `astropy`](https://www.astropy.org/acknowledging.html)

If you use COSMOS ACS imaging data in published research,  please cite the dataset Digital Object Identifier (DOI): [10.26131/IRSA178](https://www.ipac.caltech.edu/doi/irsa/10.26131/IRSA178).